In [1]:
%reset

Once deleted, variables cannot be recovered. Proceed (y/[n])? y


In [2]:
import numpy as np
import json
import sys
import scipy.io as spio
import math
import pymatgen
from pymatgen.analysis.structure_analyzer import VoronoiCoordFinder as VCF
import pdb
import pandas as pd

In [3]:
with open('Li-cmpd-data-Dec18.json') as f:
    data = json.load(f)

#mps = np.genfromtxt('mpswoNaN.txt', usecols=0, dtype = 'string')
#features = np.loadtxt('featureswoNaN.txt')
column_names = ['avg atomic mass','vol per atom','std Li neighbor count','std Li bond ionicity','Li bond ionicity','Li neighbor count','Li-Li bonds per Li','avg Li bond length','sublattice bond ionicity','sublattice neighbor count','anion framework coordination','min anion-anion sep dist','vol per anion','min Li-anion sep dist','Li number conc','mass density','min Li-Li sep dist','sublattice electronegativity','RBI','RNB']
df = pd.read_csv('full_parms_1A_for_EDC.txt', usecols=np.arange(1,21,1), header=None,delimiter='\t',names=column_names)
dfmps = pd.read_csv('full_parms_1A_for_EDC.txt',delimiter=' ',dtype = str,usecols=[0],header=None,names=['mp'])
df = df.apply(pd.to_numeric, errors='coerce')
df.head()
df = df.dropna()
print(len(df))


12735


In [106]:
from constants import cubic_equal, hex_equal, monoclinic_equal, ortho_equal, tetra1_equal, tetra2_equal, trig1_equal, trig2_equal, triclinic_equal, asym_mp
def generate_XYdata(symmetry, equals):
	xdata = []
	ydata = []
	volrat_data = []
	coord_data = []
	Gr=[]
	Gv=[]
	Gvrh=[]
	Kr=[]
	Kv=[]
	Kvrh=[]
	mps_data = []
	v_m = 1.3*pow(10,-5)
	inpfile = 'training-groups/'+symmetry + '-training-set-data.json'
	with open(inpfile, 'r') as f:
		data = json.load(f)
		for index, elem in enumerate(data):
			for index1, (mp, feature) in enumerate(zip(dfmps['mp'],df.values)):
				store_mat = True
				#for a in feature:
				#	if math.isnan(a):
				#		store_mat = False
				elastic_mat = elem['elasticity']['elastic_tensor']
				if not(np.all(np.linalg.eigvals(elastic_mat) > 0)):
					store_mat = False
					print(mp)
					print(elastic_mat)
					raise ValueError('This should have appeared earlier. No?')
				if mp == elem['task_id'] and mp not in asym_mp and store_mat:
					mps_data.append(mp)
					#xdata.append(feature)

					struc = pymatgen.Structure.from_str(data[index]['cif'],fmt="cif")
					Lisites = [i for i in range(len(struc)) if struc[i].specie.symbol=='Li']
					f = VCF(structure = struc, allow_pathological=True)
					sum = 0
					for j in Lisites:
						sum += f.get_coordination_number(j)
					
					coord_no = sum/len(Lisites)
					rad_ref = [0.59, 0.76, 0.92] # data taken from http://abulafia.mt.ic.ac.uk/shannon/radius.php?Element=Li
					coord_ref = [4., 6., 8.]
					fit = np.polyfit(coord_ref, rad_ref, 1)
					fit_fn = np.poly1d(fit)
					rad_Li = fit_fn(coord_no)
					NAV = 6.022*pow(10,23) # Avagadro_num 
					vol_plus = (4./3.)*(np.pi)*(pow(rad_Li*pow(10,-10),3))*NAV
					vol_ratio = vol_plus/v_m
					volrat_data.append(vol_ratio)
					coord_data.append(coord_no)

					Gr.append(elem['elasticity']['G_Reuss'])
					Gv.append(elem['elasticity']['G_Voigt'])
					Gvrh.append(elem['elasticity']['G_VRH'])
					Kr.append(elem['elasticity']['K_Reuss'])
					Kv.append(elem['elasticity']['K_Voigt'])
					Kvrh.append(elem['elasticity']['K_VRH'])
					#pdb.set_trace()
					#xdata.append(np.hstack((feature[0:12],feature[13:16],feature[18:])))
					xdata.append(feature)

					elastic_mat = elem['elasticity']['elastic_tensor']
					y = []
					for equal_subsets in equals:
						val = 0
						for subset in equal_subsets:
							val = val + elastic_mat[subset[0]-1][subset[1]-1]
						y.append(val / len(equal_subsets)) #averaged over all equals
					ydata.append(y)
	#xdata = pd.DataFrame(xdata,columns=column_names)
	spio.savemat(symmetry+'-data-posd-features',mdict={'mps':mps_data,'xdata':xdata,'ydata':ydata,'Gr':Gr,'Gv':Gv,'Gvrh':Gvrh,'Kr':Kr,'Kv':Kv,'Kvrh':Kvrh,'volratt':volrat_data,'coordt':coord_data})


In [107]:
generate_XYdata(symmetry = 'cubic', equals = cubic_equal)

/opt/local/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/pymatgen/analysis/structure_analyzer.py:61: UserWarning: VoronoiCoordFinder will be moved to local_env.py with pymatgen >= 2018
  warnings.warn("VoronoiCoordFinder will be moved to local_env.py"


In [6]:
dd = spio.loadmat('cubic-data-posd-features.mat')
xdatadf = pd.DataFrame(dd['xdata'],columns = column_names)
xdatadf.head()

avg atomic mass  vol per atom  std Li neighbor count  std Li bond ionicity  \
0         14.47372     10.063729                    0.0              1.060342   
1        106.64915     21.876036                    0.0              0.277318   
2         67.14900     13.081070                    0.0              0.231099   
3        136.77590     19.544446                    0.0              0.477604   
4         49.09835     12.679531                    0.0              0.133524   

   Li bond ionicity  Li neighbor count  Li-Li bonds per Li  \
0          1.785455               26.0                 8.0   
1          0.521429               14.0                 0.0   
2          1.107143               14.0                 0.0   
3          0.688571               14.0                 0.0   
4          0.781429               14.0                 0.0   

   avg Li bond length  sublattice bond ionicity  sublattice neighbor count  \
0            3.065528                  1.175692                       26.0   
1            3.253941                  0.379524                       14.0   
2            2.741371                  0.540476                       14.0   
3            3.133969                  0.583810                       14.0   
4            2.713030                  0.359524                       14.0   

   anion framework coordination  min anion-anion sep dist  vol per anion  \
0                          11.5                  3.052748      20.127459   
1                          12.0                  4.983271      87.504145   
2                           6.0                  2.968642      26.162140   
3                          12.0                  4.799539      78.177783   
4                          12.0                  4.154889      50.718126   

   min Li-anion sep dist  Li number conc  mass density  min Li-Li sep dist  \
0               1.958356        0.037263      2.388142            2.992319   
1               3.523698        0.011428      8.095201            4.983271   
2               2.570913        0.019112      8.523838            4.198263   
3               3.393733        0.012791     11.620508            4.797677   
4               2.937944        0.019717      6.429876            4.154889   

   sublattice electronegativity       RBI  RNB  
0                      3.190000  1.518641  1.0  
1                      1.450000  1.373902  1.0  
2                      2.130000  2.048458  1.0  
3                      1.580000  1.179445  1.0  
4                      1.736667  2.173510  1.0

In [46]:
features = np.loadtxt('featureswoNaN.txt')
for feature in features:
    print(feature)

[2.9705000e+01 1.4929776e+01 0.0000000e+00 4.4440200e-01 4.6000000e-01
 1.4000000e+01 9.3333330e+00 2.8648680e+00 9.2000000e-01 1.4000000e+01
 1.2000000e+01 4.3874220e+00 5.9719105e+01 2.8252780e+00 5.0235000e-02
 3.3038110e+00 2.6867280e+00 1.9000000e+00 5.0000000e-01 1.0000000e+00
 6.1444900e-01]
[6.3214515e+01 2.2838505e+01 0.0000000e+00 1.5457500e-01 1.6000000e-01
 1.4000000e+01 9.3333330e+00 3.3009780e+00 3.2000000e-01 1.4000000e+01
 1.2000000e+01 5.0553070e+00 9.1354019e+01 3.2553640e+00 3.2839000e-02
 4.5960850e+00 3.0957230e+00 1.3000000e+00 5.0000000e-01 1.0000000e+00
 4.1927100e-01]
[2.9705000e+01 1.4611959e+01 0.0000000e+00 4.1143700e-01 3.6800000e-01
 1.6000000e+01 1.2000000e+01 2.9999670e+00 6.9000000e-01 1.6000000e+01
 4.0000000e+00 3.7503400e+00 5.8447836e+01 2.7498400e+00 5.1328000e-02
 3.3756700e+00 2.7008650e+00 1.9000000e+00 5.3333300e-01 1.0000000e+00
 6.2333300e-01]
[6.6205000e+01 2.3117402e+01 0.0000000e+00 1.4491400e-01 1.5000000e-01
 1.4000000e+01 9.3333330e+00 

 -2.4345580e+00]
[ 3.3600370e+01  1.7989619e+01  1.0894100e+00  5.7076400e-01
  6.4947400e-01  1.1428571e+01  6.5714290e+00  2.9831450e+00
  7.7888900e-01  1.0800000e+01  1.2000000e+01  4.2527310e+00
  5.3968858e+01  2.5814500e+00  3.2426000e-02  3.1014230e+00
  2.8873930e+00  2.0540000e+00  8.3384600e-01  1.0582010e+00
 -5.4757400e-01]
[ 6.3280019e+01  1.3810754e+01  0.0000000e+00  3.0299600e-01
  8.8285700e-01  1.4000000e+01  0.0000000e+00  2.7914250e+00
  5.1904800e-01  1.4000000e+01  1.2000000e+01  4.2749480e+00
  5.5243017e+01  3.0228440e+00  1.8102000e-02  7.6083080e+00
  4.2749470e+00  1.8066670e+00  1.7009170e+00  1.0000000e+00
 -7.2589500e-01]
[ 3.6296590e+01  1.9990871e+01  0.0000000e+00  7.3029100e-01
  5.9818200e-01  1.2000000e+01  2.0000000e+00  3.0264760e+00
  1.0007690e+00  1.3000000e+01  1.2000000e+01  4.4104980e+00
  5.9972612e+01  2.6128220e+00  1.6674000e-02  3.0149010e+00
  3.1788970e+00  1.7400000e+00  5.9772200e-01  9.2307700e-01
 -1.1722210e+00]
[ 1.9822684e+01  

 -9.1561200e-01]
[ 3.4181667e+01  1.7607360e+01  0.0000000e+00  5.4404800e-01
  1.0836360e+00  1.2000000e+01  2.0000000e+00  2.9939030e+00
  7.8909100e-01  1.1000000e+01  1.2000000e+01  4.2716520e+00
  5.2822081e+01  2.4727060e+00  1.8931000e-02  3.2235760e+00
  3.3782470e+00  2.2400000e+00  1.3732720e+00  1.0909090e+00
 -9.4062000e-01]
[ 4.6568200e+01  2.0385869e+01  9.8473200e-01  7.0139200e-01
  1.0975440e+00  1.1666667e+01  4.3333330e+00  3.0952730e+00
  8.6363600e-01  1.1000000e+01  1.2000000e+01  4.0827870e+00
  4.7567027e+01  2.3697870e+00  2.1023000e-02  3.7931420e+00
  2.9073270e+00  2.4400000e+00  1.2708400e+00  1.0606060e+00
 -1.1868140e+00]
[ 4.8204500e+01  2.0223394e+01  0.0000000e+00  6.0380100e-01
  1.1350000e+00  1.8000000e+01  4.0000000e+00  3.4778560e+00
  4.5407400e-01  1.8000000e+01  1.2000000e+01  3.8542830e+00
  4.0446788e+01  2.6503160e+00  1.2362000e-02  3.9579690e+00
  3.9065490e+00  2.4033330e+00  2.4995920e+00  1.0000000e+00
 -9.5515700e-01]
[ 1.13269978e+02 

[ 2.5496242e+01  1.1317829e+01  8.1649700e-01  1.1299370e+00
  2.1383330e+00  2.5000000e+01  2.0000000e+00  3.1779490e+00
  1.0656840e+00  2.3750000e+01  1.1666667e+01  2.9866430e+00
  1.8863049e+01  1.9279270e+00  1.7671000e-02  3.7406920e+00
  2.4953840e+00  3.4600000e+00  2.0065360e+00  1.0526320e+00
 -2.3293170e+00]
[ 2.4973191e+01  1.0400497e+01  2.0000000e+00  1.0370670e+00
  1.5540000e+00  3.1333333e+01  4.8888890e+00  3.2853460e+00
  9.9653900e-01  2.5574468e+01  1.2000000e+01  2.9614570e+00
  1.8200869e+01  1.9854790e+00  1.5453000e-02  3.9871160e+00
  3.4427740e+00  2.8368090e+00  1.5593970e+00  1.2251800e+00
 -2.0661770e+00]
[ 2.6903257e+01  9.5726890e+00  0.0000000e+00  9.3343500e-01
  1.6840000e+00  3.2000000e+01  4.0000000e+00  3.2250020e+00
  8.9019600e-01  2.5500000e+01  1.2000000e+01  2.8796300e+00
  1.6752206e+01  1.9300370e+00  1.4923000e-02  4.6666990e+00
  3.4638870e+00  2.9300000e+00  1.8917180e+00  1.2549020e+00
 -1.0793010e+00]
[ 2.3609177e+01  1.6647724e+01  5.

 -6.8587200e-01]
[ 5.9579250e+01  2.0073505e+01  0.0000000e+00  7.2137100e-01
  7.4400000e-01  1.8000000e+01  6.0000000e+00  3.4701380e+00
  5.0444400e-01  1.8000000e+01  1.2000000e+01  3.8438930e+00
  4.0147009e+01  2.7226400e+00  1.2454000e-02  4.9284540e+00
  3.8766010e+00  2.1333330e+00  1.4748900e+00  1.0000000e+00
 -2.1903050e+00]
[ 8.1500107e+01  2.0242037e+01  0.0000000e+00  4.1067000e-01
  5.1090900e-01  1.2000000e+01  2.0000000e+00  3.0339150e+00
  5.5916700e-01  1.2000000e+01  1.2000000e+01  4.4330620e+00
  6.0726112e+01  2.6836410e+00  1.6467000e-02  6.6856380e+00
  2.8459650e+00  1.6200000e+00  9.1369700e-01  1.0000000e+00
 -7.1444500e-01]
[ 4.9796500e+01  1.5880025e+01  0.0000000e+00  4.4918600e-01
  8.2916700e-01  1.4000000e+01  4.0000000e+00  2.9244030e+00
  7.5357100e-01  1.4000000e+01  1.2000000e+01  4.4785980e+00
  6.3520101e+01  2.9547080e+00  3.1486000e-02  5.2069870e+00
  2.7425690e+00  1.9750000e+00  1.1003160e+00  1.0000000e+00
 -4.2381400e-01]
[ 3.9990962e+01  

...

 -1.6920860e+00]
[ 1.7089427e+01  1.0043152e+01  0.0000000e+00  8.7257800e-01
  1.9616000e+00  2.7000000e+01  4.0000000e+00  3.1075430e+00
  8.6338900e-01  2.6173913e+01  7.7500000e+00  2.7835820e+00
  1.8203213e+01  2.0996000e+00  2.0601000e-02  2.8255070e+00
  3.3668100e+00  3.1121740e+00  2.2719780e+00  1.0315610e+00
 -2.0079810e+00]
[ 3.2942825e+01  1.1233536e+01  3.2015620e+00  9.1772700e-01
  1.7058720e+00  2.8750000e+01  3.0000000e+00  3.2808960e+00
  9.3610400e-01  2.3958333e+01  1.2000000e+01  3.0351690e+00
  1.9658687e+01  1.8774830e+00  1.2717000e-02  4.8694870e+00
  3.6010160e+00  2.9162500e+00  1.8223090e+00  1.2000000e+00
 -1.9959200e+00]
[ 2.6287686e+01  1.6228476e+01  5.7735000e-01  8.8565600e-01
  1.8054050e+00  1.8500000e+01  0.0000000e+00  3.1308170e+00
  1.0714450e+00  1.5759259e+01  4.2187500e+00  2.5832620e+00
  2.8399834e+01  1.9116920e+00  2.2010000e-03  2.6897600e+00
  7.6510030e+00  2.7866670e+00  1.6850190e+00  1.1739130e+00
 -2.1535010e+00]
[ 2.5819304e+01  

 -2.4526370e+00]
[ 1.3595256e+01  9.4652140e+00  0.0000000e+00  6.4528400e-01
  1.5836730e+00  2.5000000e+01  1.0000000e+00  2.8376240e+00
  7.5742700e-01  2.8613636e+01  9.6842110e+00  2.9719150e+00
  2.2417611e+01  2.1026740e+00  2.3480000e-03  2.3850410e+00
  3.4084710e+00  2.7088640e+00  2.0908610e+00  8.7370900e-01
 -1.6562520e+00]
[ 5.2618979e+01  1.3187633e+01  0.0000000e+00  1.0350950e+00
  1.0708330e+00  1.8000000e+01  0.0000000e+00  2.9575520e+00
  8.8893100e-01  1.9076923e+01  9.8125000e+00  3.0718340e+00
  2.3078357e+01  1.9207470e+00  5.4160000e-03  6.6254360e+00
  5.3300020e+00  2.5971150e+00  1.2046300e+00  9.4354800e-01
 -3.2129310e+00]
[ 1.8484500e+01  1.1612995e+01  0.0000000e+00  8.1588600e-01
  1.8525000e+00  2.5000000e+01  2.0000000e+00  3.2033880e+00
  9.0842100e-01  2.2800000e+01  8.1428570e+00  2.7946630e+00
  1.9907991e+01  2.0212800e+00  1.4352000e-02  2.6430320e+00
  3.0135430e+00  3.0360000e+00  2.0392530e+00  1.0964910e+00
 -2.2505070e+00]
[ 3.5731650e+01  

 -2.2926810e+00]
[ 2.8930584e+01  1.1035425e+01  3.2015620e+00  9.9649700e-01
  1.5976150e+00  2.8750000e+01  3.0000000e+00  3.2522700e+00
  1.0059270e+00  2.4041667e+01  1.2000000e+01  3.0186150e+00
  1.9311995e+01  1.8820410e+00  1.2945000e-02  4.3531840e+00
  3.5208960e+00  2.8241670e+00  1.5882010e+00  1.1958410e+00
 -2.8192010e+00]
[ 2.8970374e+01  1.0588064e+01  3.4641020e+00  9.7099400e-01
  1.6211820e+00  2.9000000e+01  3.0000000e+00  3.2124970e+00
  9.5175600e-01  2.4916667e+01  1.2000000e+01  2.9813650e+00
  1.8529112e+01  1.9020230e+00  1.3492000e-02  4.5433520e+00
  3.5063220e+00  2.8554170e+00  1.7033590e+00  1.1638800e+00
 -2.1814930e+00]
[ 2.5768978e+01  9.9670660e+00  3.2015620e+00  9.3923200e-01
  1.6664860e+00  2.9250000e+01  3.0000000e+00  3.1671750e+00
  9.2238200e-01  2.5541667e+01  1.2000000e+01  2.9179510e+00
  1.7442366e+01  1.8441890e+00  1.4333000e-02  4.2930780e+00
  3.3322410e+00  2.8800000e+00  1.8067210e+00  1.1451880e+00
 -2.1319510e+00]
[ 2.6211382e+01  

 -2.3958440e+00]
[ 1.7656524e+01  1.0635266e+01  1.0327960e+00  9.8411100e-01
  1.6822970e+00  2.7333333e+01  5.3333330e+00  3.1597430e+00
  1.0515850e+00  2.4600000e+01  7.7142860e+00  2.8098790e+00
  1.9751209e+01  2.0065690e+00  2.1698000e-02  2.7567390e+00
  3.1651180e+00  2.9860000e+00  1.5997720e+00  1.1111110e+00
 -2.5591660e+00]
[ 1.7726289e+01  1.0464337e+01  5.1639800e-01  9.7397500e-01
  1.7365280e+00  2.6666667e+01  5.3333330e+00  3.1232080e+00
  1.0102730e+00  2.5600000e+01  8.5714290e+00  2.8575630e+00
  1.9433769e+01  1.9967470e+00  2.2053000e-02  2.8128400e+00
  3.0649570e+00  3.0140000e+00  1.7188690e+00  1.0416670e+00
 -2.5341090e+00]
[ 3.6763621e+01  1.0777708e+01  2.2173560e+00  9.8352100e-01
  1.7620430e+00  2.5250000e+01  4.0000000e+00  3.1196720e+00
  9.2393300e-01  2.4312500e+01  1.2000000e+01  2.9604900e+00
  1.7962847e+01  2.0287330e+00  1.8557000e-02  5.6640980e+00
  3.5126490e+00  3.0718750e+00  1.9071110e+00  1.0385600e+00
 -2.4088920e+00]
[ 2.3217466e+01  

 -2.3834730e+00]
[ 1.8366207e+01  1.1067639e+01  1.2292730e+00  9.5905800e-01
  1.7535770e+00  2.6800000e+01  4.4000000e+00  3.1777150e+00
  1.0410910e+00  2.3142857e+01  7.7857140e+00  2.8426250e+00
  2.0554187e+01  2.0191610e+00  1.7376000e-02  2.7555190e+00
  3.1632280e+00  2.9366670e+00  1.6843660e+00  1.1580250e+00
 -2.4172130e+00]
[ 1.7766350e+01  1.0802756e+01  4.9236600e-01  9.4186000e-01
  1.7681330e+00  2.7666667e+01  5.3333330e+00  3.1863560e+00
  9.9448500e-01  2.4750000e+01  7.9285710e+00  2.8299480e+00
  2.0062261e+01  2.0132980e+00  2.1362000e-02  2.7308790e+00
  3.0466700e+00  3.0440000e+00  1.7779390e+00  1.1178450e+00
 -2.4163390e+00]
[ 2.0835402e+01  1.2132742e+01  0.0000000e+00  9.7834500e-01
  1.5315380e+00  2.6000000e+01  0.0000000e+00  3.2390310e+00
  1.1631360e+00  2.0920000e+01  6.6428570e+00  2.8189420e+00
  2.2532234e+01  2.1845710e+00  3.1700000e-03  2.8515550e+00
  4.8537160e+00  2.6156000e+00  1.3167320e+00  1.2428300e+00
 -2.3849350e+00]
[ 2.0905168e+01  

In [47]:
dfmps['mp'].shape

(12745,)

In [48]:
df.values.shape

(12735, 20)

In [50]:
features.shape

(12732, 21)

In [52]:
len(df)

12735

In [54]:
df.iloc[1]

avg atomic mass                 11.795200
vol per atom                    13.011621
std Li neighbor count            0.000000
std Li bond ionicity             0.686661
Li bond ionicity                 1.607742
Li neighbor count               17.000000
Li-Li bonds per Li               3.000000
avg Li bond length               3.160305
sublattice bond ionicity         0.507073
sublattice neighbor count       20.500000
anion framework coordination    10.500000
min anion-anion sep dist         3.529253
vol per anion                   32.529053
min Li-anion sep dist            2.081866
Li number conc                   0.015371
mass density                     1.505264
min Li-Li sep dist               2.804930
sublattice electronegativity     2.795000
RBI                              3.170631
RNB                              0.829268
Name: 1, dtype: float64

/opt/local/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/pymatgen/analysis/structure_analyzer.py:61: UserWarning: VoronoiCoordFinder will be moved to local_env.py with pymatgen >= 2018
  warnings.warn("VoronoiCoordFinder will be moved to local_env.py"


array([[(array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object), array([[None]], dtype=object))]],
      dtype=[('avg atomic mass', 'O'), ('vol per atom', 'O'), ('std Li neighbor count', 'O'), ('std Li bond ionicity', 'O'), ('Li bond ionicity', 'O'), ('Li neighbor count', 'O'), ('Li-Li bonds per Li', 'O'), ('avg Li bond length', 'O'), ('sublattice bond ionicity', 'O'), ('sublattice neighbor count', 'O'), ('anion framework coordination', 'O'), ('min anion-anion se

array([[ 14.47372 ,  10.063729,   0.      , ...,   3.19    ,   1.518641,
          1.      ],
       [106.64915 ,  21.876036,   0.      , ...,   1.45    ,   1.373902,
          1.      ],
       [ 67.149   ,  13.08107 ,   0.      , ...,   2.13    ,   2.048458,
          1.      ],
       ...,
       [ 65.257303,  21.926327,   0.      , ...,   2.614286,   2.066642,
          0.56    ],
       [ 17.420991,  10.318008,   0.894427, ...,   3.191538,   1.63513 ,
          0.986471],
       [ 43.188705,  19.861608,   0.      , ...,   1.833333,   0.847703,
          0.9375  ]])

avg atomic mass  vol per atom  std Li neighbor count  \
0          14.473720     10.063729               0.000000   
1         106.649150     21.876036               0.000000   
2          67.149000     13.081070               0.000000   
3         136.775900     19.544446               0.000000   
4          49.098350     12.679531               0.000000   
5          40.471000     18.393230               0.000000   
6          36.368294     15.512306               0.000000   
7          15.313000     14.544561               1.603567   
8          97.447583     21.567169               0.000000   
9          52.686363     29.516419               0.000000   
10         15.622500     20.421199               0.000000   
11         28.768570     10.024234               0.000000   
12         55.620143     23.599735               0.000000   
13         22.585850     11.155948               0.000000   
14         34.916000     16.999210               0.000000   
15         49.492500     17.214719               0.000000   
16         47.670494     13.117353               0.000000   
17         20.675207     12.652437               0.000000   
18        101.657000     13.361050               0.000000   
19         31.777778     17.739760               0.000000   
20         81.979960     34.027829               0.000000   
21         80.075133     26.778168               0.000000   
22         13.315667      9.534936               2.000000   
23         51.549250     12.820370               0.000000   
24         10.695400      9.670663               0.000000   
25         44.823000     24.882218               0.000000   
26         36.368294     14.042019               0.000000   
27         21.195000     17.101198               0.000000   
28         58.645750     24.259314               0.000000   
29         52.837576     11.166922               0.000000   
..               ...           ...                    ...   
141       110.702105     20.463794               0.000000   
142        87.848500     24.215570               0.000000   
143        14.725413     15.148035               1.732051   
144        77.501750     23.759899               0.000000   
145        12.635923      8.989376               0.000000   
146        38.279316     12.004416               0.000000   
147        37.549098     13.745425               0.000000   
148        61.864000     13.923754               0.000000   
149        23.056771     11.101390               0.000000   
150        40.952144     13.760354               0.000000   
151        13.335667     16.073406               0.000000   
152        61.346250     19.921641               0.000000   
153        26.306167      9.931991               2.000000   
154        35.195250     20.618737               0.000000   
155        19.023857      9.404618               0.975900   
156        21.701250      8.840134               0.707107   
157        27.167125     18.256555               0.000000   
158        14.450802      9.543728               0.000000   
159       104.956742     19.765167               0.000000   
160        19.213733     11.404640               0.000000   
161        44.000200     13.261664               0.000000   
162        22.745818     10.794296               1.603567   
163        20.258894     10.362218               1.154701   
164        29.568676     11.144214               0.000000   
165        58.976142     13.756753               0.000000   
166        39.785000     17.559891               0.000000   
167       101.012000     14.063685               0.000000   
168        65.257303     21.926327               0.000000   
169        17.420991     10.318008               0.894427   
170        43.188705     19.861608               0.000000   

     std Li bond ionicity  Li bond ionicity  Li neighbor count  \
0                1.060342          1.785455          26.000000   
1                0.277318          0.521429          14.000000   
2                0.23109